In [1]:
import matplotlib.pyplot as plt
import pandas as pd
import geopandas as gpd
import contextily as cx
from shapely import wkt
import networkx as nx
from pyvis.network import Network
import altair as alt
import nx_altair as nxa
import plotly.express as px
import pycountry_convert as pc
import folium

In [2]:
filepath=r'Datasets for IV\60dde6d7-en\QITS-2023-1-EN-20240216T090213.csv'
df=pd.read_csv(filepath)
df.head()

LOCATION Reporter country FLOW     Flow PARTNER Partner country FREQUENCY  \
0      AUS        Australia  EXP  Exports     AUT         Austria         A   
1      AUS        Australia  EXP  Exports     AUT         Austria         A   
2      AUS        Australia  EXP  Exports     AUT         Austria         A   
3      AUS        Australia  EXP  Exports     AUT         Austria         A   
4      AUS        Australia  EXP  Exports     AUT         Austria         A   

  Frequency  TIME  Time Unit Code       Unit  PowerCode Code PowerCode  \
0    Annual  2010  2010       USD  US Dollar               0     Units   
1    Annual  2011  2011       USD  US Dollar               0     Units   
2    Annual  2012  2012       USD  US Dollar               0     Units   
3    Annual  2013  2013       USD  US Dollar               0     Units   
4    Annual  2014  2014       USD  US Dollar               0     Units   

   Reference Period Code  Reference Period     Value  Flag Codes  Flags  
0                    NaN               NaN  62852134         NaN    NaN  
1                    NaN               NaN  73144918         NaN    NaN  
2                    NaN               NaN  71483059         NaN    NaN  
3                    NaN               NaN  67897422         NaN    NaN  
4                    NaN               NaN  61114752         NaN    NaN

In [3]:
df=df.drop(columns=['Unit Code', 'Unit', 'PowerCode Code', 'PowerCode',
       'Reference Period Code', 'Reference Period', 'Flag Codes','Flags'])

df.head()

LOCATION Reporter country FLOW     Flow PARTNER Partner country FREQUENCY  \
0      AUS        Australia  EXP  Exports     AUT         Austria         A   
1      AUS        Australia  EXP  Exports     AUT         Austria         A   
2      AUS        Australia  EXP  Exports     AUT         Austria         A   
3      AUS        Australia  EXP  Exports     AUT         Austria         A   
4      AUS        Australia  EXP  Exports     AUT         Austria         A   

  Frequency  TIME  Time     Value  
0    Annual  2010  2010  62852134  
1    Annual  2011  2011  73144918  
2    Annual  2012  2012  71483059  
3    Annual  2013  2013  67897422  
4    Annual  2014  2014  61114752

In [4]:
df.replace('Korea','South Korea',inplace=True)

In [5]:
df['Reporter country'].unique()

array(['Australia', 'Austria', 'Belgium', 'Canada', 'Czechia', 'Denmark',
       'Finland', 'France', 'Germany', 'Greece', 'Hungary', 'Iceland',
       'Ireland', 'Italy', 'Japan', 'South Korea', 'Luxembourg', 'Mexico',
       'Netherlands', 'New Zealand', 'Norway', 'Poland', 'Portugal',
       'Slovak Republic', 'Spain', 'Sweden', 'Switzerland', 'Türkiye',
       'United Kingdom', 'United States', 'Chile', 'Estonia', 'Israel',
       'Slovenia', 'European Union (27 countries)',
       "China (People's Republic of)", 'Russia', 'South Africa', 'India',
       'Brazil', 'Lithuania', 'Latvia', 'Colombia', 'Indonesia',
       'European Union (28 countries)', 'Costa Rica'], dtype=object)

In [6]:
def country_to_continent(country_name):
    try:
        country_alpha2 = pc.country_name_to_country_alpha2(country_name)
        country_continent_code = pc.country_alpha2_to_continent_code(country_alpha2)
        country_continent_name = pc.convert_continent_code_to_continent_name(country_continent_code)
    except:
        country_continent_name = 'Unknown'
    return country_continent_name

In [7]:
df['Reporter Continent']=df['Reporter country'].apply(country_to_continent)

c:\Users\Divya\anaconda3\Lib\site-packages\pycountry\db.py:51: UserWarning: Country's official_name not found. Country name provided instead.
  warnings.warn(warning_message, UserWarning)
c:\Users\Divya\anaconda3\Lib\site-packages\pycountry\db.py:51: UserWarning: Country's common_name not found. Country name provided instead.
  warnings.warn(warning_message, UserWarning)


In [8]:
df['Reporter Continent'].unique()

array(['Oceania', 'Europe', 'North America', 'Asia', 'South America',
       'Unknown', 'Africa'], dtype=object)

In [9]:
grouped = df.groupby(df.Frequency)
df_annual = grouped.get_group("Annual")
df_quarter = grouped.get_group("Quarterly")

In [10]:
flow='Exports'
freq='Quarterly'
if freq == 'Annual':
    df_plot = df_annual[df_annual['Flow']==flow]
if freq == 'Quarterly':
    df_plot = df_quarter[df_quarter['Flow']==flow]
df_plot.head()

LOCATION Reporter country FLOW     Flow PARTNER Partner country  \
17548      AUS        Australia  EXP  Exports     AUT         Austria   
17549      AUS        Australia  EXP  Exports     AUT         Austria   
17550      AUS        Australia  EXP  Exports     AUT         Austria   
17551      AUS        Australia  EXP  Exports     AUT         Austria   
17552      AUS        Australia  EXP  Exports     AUT         Austria   

      FREQUENCY  Frequency     TIME     Time     Value Reporter Continent  
17548         Q  Quarterly  2010-Q1  Q1-2010  10120641            Oceania  
17549         Q  Quarterly  2010-Q2  Q2-2010  16640640            Oceania  
17550         Q  Quarterly  2010-Q3  Q3-2010  21195674            Oceania  
17551         Q  Quarterly  2010-Q4  Q4-2010  14895179            Oceania  
17552         Q  Quarterly  2011-Q1  Q1-2011  14512880            Oceania

In [14]:
fig = px.scatter_geo(df_plot,
                     locations="LOCATION",
                     color='Reporter Continent',
                     hover_name="Reporter country",
                     size="Value",
                     animation_frame="Time",
                     projection="natural earth")

#plt.title(f'{flow} over time')
fig.show()


In [30]:
from mpl_toolkits.basemap import Basemap as Basemap

plt.figure(figsize = (10,9))

basemap = Basemap(
    projection = 'merc',
    llcrnrlon = -180, 
    urcrnrlon = -50,     
    llcrnrlat = -10,  
    urcrnrlat = 70,    
    lat_ts = 0,
    resolution = 'l',
    suppress_ticks = True)

<Figure size 1000x900 with 0 Axes>

In [ ]:
basemap_x, basemap_y = basemap(df_airports['LONGITUDE'].values, 
                               df_airports['LATITUDE'].values)

# References:
- https://stackoverflow.com/questions/55910004/get-continent-name-from-country-using-pycountry